### Import necessary modules

In [1]:
import numpy as np
import pandas as pd
import scipy as sp
import matplotlib.pyplot as plt
import sklearn as sk
import datetime
import calendar
from jupyter_dash import JupyterDash
import dash
from dash import Dash, html, dcc, Input, Output
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import requests
import io
from plotly.subplots import make_subplots

<frozen importlib._bootstrap>:228: RuntimeWarning: scipy._lib.messagestream.MessageStream size changed, may indicate binary incompatibility. Expected 56 from C header, got 64 from PyObject


### Set up Google Cloud BigQuery Request

In [2]:
from google.cloud import bigquery
!export GOOGLE_APPLICATION_CREDENTIALS="cse6242project-377400-2f98c9def7f8.json"
!gcloud auth activate-service-account --key-file cse6242project-377400-2f98c9def7f8.json

zsh:1: command not found: gcloud


In [3]:
import os

os.environ["GOOGLE_APPLICATION_CREDENTIALS"]="cse6242project-377400-2f98c9def7f8.json"

In [4]:
import pandas as pd

In [5]:
# Initialize a BigQuery client
client = bigquery.Client()

### Request Data From BigQuery

In [6]:
table_ref = client.dataset('cse6242gbq').table('counts_table')
table = client.get_table(table_ref)

schema_df = pd.DataFrame([field.to_api_repr() for field in table.schema])

In [7]:
query = """
        SELECT * 
        FROM `cse6242project-377400.cse6242gbq.counts_table` 
        """
df = client.query(query).to_dataframe()
df.head(5)

date      time                       view  car  motorcycle  \
0  2023-02-15  00:19:27  View_from_Tuas_Checkpoint    0           0   
1  2023-02-15  02:17:38  View_from_Tuas_Checkpoint    0           0   
2  2023-02-15  03:12:21  View_from_Tuas_Checkpoint    0           0   
3  2023-02-15  04:15:08  View_from_Tuas_Checkpoint    0           0   
4  2023-02-15  05:13:14  View_from_Tuas_Checkpoint    0           0   

   large_vehicle  
0              0  
1              0  
2              0  
3              0  
4              0

### Data Preprocessing

In [8]:
df = df.sort_values(by=['date']).reset_index(drop=True) #sort the dataframe
df['date'] = pd.to_datetime(df['date'], format = "%Y-%m-%d") #convert to required format
df['day'] = df['date'].dt.day_name()

#Map new labels to view column
df['vehicle'] = df['car'] + df['large_vehicle'] + df['motorcycle']
transfer = {"View_from_Second_Link_at_Tuas_to_sg": 'Johor-Tuas', 
            "View_from_Second_Link_at_Tuas_to_jh": 'Tuas-Johor',
            "View_from_Tuas_Checkpoint_to_sg": 'Johor-Tuas',
            "View_from_Tuas_Checkpoint_to_jh": 'Tuas-Johor',
            "View_from_Woodlands_Causeway_Towards_Johor_to_sg": 'Johor-Woodlands',
            "View_from_Woodlands_Causeway_Towards_Johor_to_jh": 'Woodlands-Johor',
            "View_from_Woodlands_Checkpoint_Towards_BKE_to_sg": 'Johor-Woodlands',
            "View_from_Woodlands_Checkpoint_Towards_BKE_to_jh": 'Woodlands-Johor'}

new_table = df.replace({'view':transfer})

#Filter the data
options = ['Johor-Woodlands','Woodlands-Johor','Johor-Tuas','Tuas-Johor']
final_df = new_table[new_table['view'].isin(options)]

### Create data processing functions

In [9]:
from datetime import datetime, timedelta

#As data is scraped at different times every hour, any values before 30 minutes after the hour will be rounded down
# and any values after 30 minutes will be rounded up. I.e 11:50 -> 12:00 and 9:10 -> 9:00

def hour_rounder(t):
    if int(t.minute)>= 30:
        time_1 = str(int(t.hour)+1)
        if len(time_1) == 1:
            return "0"+time_1+":00"
        else:
            return str(time_1)+":00"
    else:
        if len(str(t.hour)) == 1:
            return "0"+str(t.hour)+":00"
        else:
            return str(t.hour)+":00"

In [10]:
def peak_hours(t):
    peak = ['07:00', "08:00", '09:00', "17:00", "18:00", "19:00"]
    if t in peak:
        return 1
    else:
        return 0

In [11]:
def weekend(w):
    end = ['Saturday', 'Sunday']
    if w in end:
        return 1
    else:
        return 0

In [12]:
def convert_date(date):
    return datetime.strptime(date, "%Y-%m-%d").strftime('%A')    
print(convert_date("2013-04-11"))   

Thursday


In [13]:
#Apply hour_rounder function to dataframe
final_df.loc[:,'hour'] = final_df.loc[:,'time'].apply(hour_rounder)

/var/folders/w8/7fvtd_nn7235fgdf50g59c5h0000gn/T/ipykernel_82351/124420089.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  final_df.loc[:,'hour'] = final_df.loc[:,'time'].apply(hour_rounder)


Group the data by the average vehicle count per view, day of the week and hour

In [14]:
final_table = final_df.groupby(['view', 'day', 'hour']).mean().reset_index().loc[:,['day', 'hour','view', 'vehicle']]
final_table['vehicle'] = final_table['vehicle'].apply(lambda x: round(x))
display(final_table.head(3))

day   hour        view  vehicle
0  Friday  00:00  Johor-Tuas        0
1  Friday  01:00  Johor-Tuas        1
2  Friday  02:00  Johor-Tuas        1

### Create function to convert vehicle counts to categories:
- Between 0-2 vehicles -> "No Traffic"
- Between 2-4 vehicles -> "Low Traffic"
- Between 4-6 vehicles -> "Minimal Traffic"
- Between 6-8 vehicles -> "Moderate Traffic"
- 8+ vehicles -> "Heavy Traffic"


In [15]:
def vehicle_cat(v):
    if v >= 0 and v < 2:
        return 0
    elif v >= 2 and v < 4:
        return 1
    elif v >= 4 and v < 6:
        return 2
    elif v >= 6 and v < 8:
        return 3
    else:
        return 4    

In [16]:
#Prep data for Model
final_table.loc[:,'peak'] = final_table.loc[:,'hour'].apply(peak_hours)
final_table.loc[:,'peak'] = final_table.loc[:,'peak'].astype('category')
final_table.loc[:,'weekend'] = final_table.loc[:,'day'].apply(weekend)
final_table.loc[:,'weekend'] = final_table.loc[:,'weekend'].astype('category')
final_table.loc[:,'cat'] = final_table.loc[:,'vehicle'].apply(vehicle_cat)
final_table.loc[:,'cat'] = final_table.loc[:,'cat'].astype('category')
display(final_table.head(3))

day   hour        view  vehicle peak weekend cat
0  Friday  00:00  Johor-Tuas        0    0       0   0
1  Friday  01:00  Johor-Tuas        1    0       0   0
2  Friday  02:00  Johor-Tuas        1    0       0   0

### Neural Network Machine Learning Model: Training and Testing

Split the data and create dummy variables for each category

In [17]:
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import cross_val_score, GridSearchCV, cross_validate, train_test_split
from sklearn.metrics import accuracy_score, classification_report

In [18]:
X = final_table.loc[:,['day', 'hour','view']]
Y = final_table.loc[:,'cat']

X = pd.get_dummies(X)
X.loc[:,['peak', 'weekend']] = final_table.loc[:,['peak', 'weekend']]
display(X.head(3))

x_train, x_test, y_train, y_test = train_test_split(X, Y, train_size=0.7,
                                                            test_size=0.3,
                                                            shuffle=True, random_state=13)

day_Friday  day_Monday  day_Saturday  day_Sunday  day_Thursday  \
0           1           0             0           0             0   
1           1           0             0           0             0   
2           1           0             0           0             0   

   day_Tuesday  day_Wednesday  hour_00:00  hour_01:00  hour_02:00  ...  \
0            0              0           1           0           0  ...   
1            0              0           0           1           0  ...   
2            0              0           0           0           1  ...   

   hour_21:00  hour_22:00  hour_23:00  hour_24:00  view_Johor-Tuas  \
0           0           0           0           0                1   
1           0           0           0           0                1   
2           0           0           0           0                1   

   view_Johor-Woodlands  view_Tuas-Johor  view_Woodlands-Johor  peak  weekend  
0                     0                0                     0     0        0  
1                     0                0                     0     0        0  
2                     0                0                     0     0        0  

[3 rows x 38 columns]

In [19]:
#create basic model
clf = MLPClassifier(solver='lbfgs', alpha=0.65, hidden_layer_sizes=(4,3), random_state=2, max_iter=5000)
clf.fit(x_train, y_train)
y_pred = clf.predict(x_test)
print(accuracy_score(y_test, y_pred))

0.7238095238095238
[130  40  19  14   7]
[120  49  18  10  13]


In [20]:
#Create GridSearch grid to find optimal parameters
parameters = {"solver":['lbfgs', 'adam', 'sgd'],
             'alpha':[0.005, 0.05, 0.5,1,1.5, 2],
             'hidden_layer_sizes':[(4,3), (5,3), (6,3)]}
grid = GridSearchCV(clf, parameters).fit(x_train, y_train)
print(grid.best_params_)
print(grid.best_score_)

{'alpha': 1.5, 'hidden_layer_sizes': (5, 3), 'solver': 'lbfgs'}
0.7341047759309911


In [21]:
clf = MLPClassifier(solver=grid.best_params_['solver'], alpha=grid.best_params_['alpha'], 
                    hidden_layer_sizes=grid.best_params_['hidden_layer_sizes'], 
                    random_state=8, max_iter=4000)

clf.fit(x_train, y_train)
y_pred = clf.predict(x_test)
print(accuracy_score(y_test, y_pred))

0.7380952380952381
[124  41  30   9   6]
[120  49  18  10  13]


### Create function to process user inputs from Dash Dropdowns
- This function takes date, hour and direction from the users input.
- Date is converted to the day of the week and determines if it is a weekday or weekend
- Hour is converted to string and determines if it is during peak hours
- This row is applied to the NN model that was created above and a predicted category is returned

In [22]:
h = '17:00'
v = 'Woodlands-Johor'

def create_row(date_d, hour, view):
    if date_d is None:
        date_d = "2023-04-11"
    if hour is None:
        hour = "09:00"
    if view is None:
        view = "Johor-Tuas"
    
    features = x_train.columns
    d_dict = {}
    day = datetime.strptime(date_d, "%Y-%m-%d").strftime('%A')
    hour = str(hour)
    view = str(view)
    col_day = "day_" + day
    col_hour = 'hour_'+h
    col_view = 'view_'+view
    
    for i in features:
        if i == col_day or i == col_hour or i == col_view:
            d_dict[i] = [1]
        else:
            d_dict[i] = [0]
    end = ['Saturday', 'Sunday']
    peak = ['07:00', "08:00", '09:00', "17:00", "18:00", "19:00"]
    
    if day in end:
        d_dict['weekend'] = 1
    if hour in peak:
        d_dict['peak'] = 1   
    result = pd.DataFrame.from_dict(d_dict, orient='columns')
    for i in features:
        result[i] = result[i].astype('category')
    return result   

In [23]:
#Test the function
print(clf.predict(create_row("2013-04-15", h, v)))  
print(clf.predict(create_row("2013-04-17", None, None)))     

[2]
[1]


### Create the figures to be loaded to the dashboard

In [24]:
paths = ["M 0.2 0.35 L 0.48 0.52 L 0.52 0.50",
        "M 0.25 0.75 L 0.475 0.52 L 0.52 0.52",
        "M 0.5 0.9 L 0.485 0.52 L 0.515 0.52",
        "M 0.75 0.75 L 0.485 0.52 L 0.52 0.51",
        "M 0.8 0.35 L 0.48 0.50 L 0.52 0.52"]

figs = []
values_ = ["No Traffic on Johor-Singapore Causeway", "Low Traffic on Johor-Singapore Causeway", "Johor-Singapore Causeway Slightly Busy", 
           "Johor-Singapore Causeway Moderately Busy", "Busiest Time to Travel on Johor-Singapore Causeway"]

for i in range(5):
    plot_bgcolor = "#def"
    colors = ["#f25829", "#f2a529", "#eff229", "#85e043", "#2bad4e","rgba(0,0,0,0)"] 
    quadrant_text = ["<b>Heavy</b>", "<b>Moderate</b>", "<b>Mild</b>", "<b>Low</b>", "<b>None</b>",""]
    n_quadrants = len(colors) - 1
    figure_1 = go.Figure(
        data=[
            go.Pie(
                values=[14,14,14,14,14,30],
                rotation=130,
                hole=0.75,
                marker_colors=colors,
                marker_line={"width":2, "color":"white"},
                textinfo="none",
                text=quadrant_text,
                hoverinfo="text"
            ),
        ],
        layout=go.Layout(
            showlegend=False,
            margin=dict(b=0,t=30,l=10,r=10),
            width=500,
            height=350,
            paper_bgcolor="rgba(0,0,0,0)",
            annotations=[
                go.layout.Annotation(
                    text=f"<b>{values_[i]}</b>",
                    x=0.5, xanchor="center", xref="paper",
                    y=0.1, yanchor="bottom", yref="paper",
                    showarrow=False,
                    font= {"size":15, "color":"#333"}
                )
            ]
        )
    )
    figure_1.update_layout(shapes=[dict(type='path',
                                        path=paths[i],
                                       fillcolor="#333"), 
                                                  go.layout.Shape(
                    type="circle",
                    x0=0.48, x1=0.52,
                    y0=0.48, y1=0.54,
                    fillcolor="#333",
                    line_color="#333",
                )])
    figs.append(figure_1)

### Create function that takes the dropdown inputs and applies the NN model and returns the associated figure

In [25]:
# x = list of [model, date, hour, view]
def predicted_figure(x):
    
    result = create_row(x[1], x[2], x[3])
    pred_val = clf.predict(result)[0]
    
    return figs[pred_val]


In [26]:
#Test the function
b = [clf, "2023-04-27", "09:00", "Johor-Tuas"]
predicted_figure(b)

### The dashboard starting values will be automatically to today's date

In [27]:
from datetime import date
t = str(date.today()).split('-')
today = []

for i in t:
    if t[0] =='0':
        today.append(int(t[1:]))
    else:
        today.append(int(i))

In [28]:
starter_variables = [clf, str(date.today()), "07:00", "Tuas-Johor"]
fig = predicted_figure(starter_variables)
fig.show()

### Create starter barplots for each direction for the initial dashboard

In [29]:
day_today = convert_date(str(date.today()))
df_filter = final_table[final_table['day']==day_today]

color_map = {0:"#2bad4e", 1:"#85e043", 2:"#eff229", 3:"#f2a529", 4:"#f25829"}


bar_day = make_subplots(shared_yaxes="all", rows=2, cols=2, start_cell="bottom-left", subplot_titles=("Johor-Tuas", 
                                                                              "Tuas-Johor", 
                                                                              "Johor-Woodlands",
                                                                                "Johor-Woodlands"))
f1 = df_filter[df_filter['view']=='Johor-Tuas']
c1 = pd.Series(f1['cat']).map(color_map)
bar_day.add_trace(go.Bar(x=f1['hour'], y=f1['vehicle'], name='Johor-Tuas', showlegend=False, marker={'color':c1}),
              row=1, col=1)

f2 = df_filter[df_filter['view']=='Tuas-Johor']
c2 = pd.Series(f2['cat']).map(color_map)
bar_day.add_trace(go.Bar(x=f2['hour'], y=f2['vehicle'], name='Tuas-Johor', showlegend=False, marker={'color':c2}),
              row=1, col=2)
f3 = df_filter[df_filter['view']=='Johor-Woodlands']
c3 = pd.Series(f3['cat']).map(color_map)
bar_day.add_trace(go.Bar(x=f3['hour'], y=f3['vehicle'], name='Johor-Woodlands', showlegend=False, marker={'color':c3}),
              row=2, col=1)
f4 = df_filter[df_filter['view']=='Woodlands-Johor']
c4 = pd.Series(f4['cat']).map(color_map)
bar_day.add_trace(go.Bar(x=f4['hour'], y=f4['vehicle'], name='Johor-Woodlands', showlegend=False, marker={'color':c4}),
              row=2, col=2)

val_d = date.today().strftime("%d %B, %Y")
day_d = date.today().strftime("%A")
tex = "Predicted 24 Hour Traffic Trend on: " + day_d + ", " + str(val_d)


bar_day.update_layout(title_text=tex, paper_bgcolor="rgba(0,0,0,0)", plot_bgcolor="rgba(0,0,0,0)")
bar_day.update_xaxes(tickangle=45)

bar_day.show()


### Create the Dashboard:

In [37]:
app = JupyterDash(__name__)

app.title = 'CSE6242 Dashboard'
app.layout = html.Div([
    html.Div([
    dcc.DatePickerSingle(
    id='my_date_picker_single',
        min_date_allowed=date(2023, 4, 11),
        max_date_allowed=date(2024, 4, 11),
        initial_visible_month=date(today[0],today[1], today[2]),
        date=date(today[0],today[1], today[2])
    ),
    html.Div(id='output-container-date-picker-single')],
        style={'width':'20%','height':'20px', 
               'padding-left':'20%',
               'display':'inline-block',
               "align-items":'center', 
               'justify-content':'center'}),
    html.Div([dcc.Dropdown(id='hours_dropdown_id',
                                     options=['00:00', '01:00', '02:00', '03:00', '04:00', '05:00', '06:00', '07:00', '08:00', '09:00', 
                         '10:00', '11:00', '12:00', '13:00', '14:00', '15:00', '16:00', '17:00', '18:00','19:00',
                         '20:00', '21:00', '22:00', '23:00'],
                                     value='07:00', clearable=False),html.Label("Estimated Leave Time")],
    style={'width':'17%','height':'20px', 'padding-left':'0%',
                                                 'display':'inline-block'}),
    html.Div([dcc.Dropdown(id='direction_id',
                                     options=['Johor-Tuas','Johor-Woodlands',
                                             'Tuas-Johor', 'Woodlands-Johor'],
                                     value="Tuas-Johor", clearable=False),html.Label("Direction")],
    style={'width':'15%','height':'20px', 'padding-left':'5%','display':'inline-block',"align-items":'center', 
                    'justify-content':'center'}),
    html.Div(dcc.Graph(id='final_output', figure=fig),
             style={'width':'100%', 'display': "flex", "align-items":'center', 
                    'justify-content':'center'}),
    html.Div(dcc.Graph(id='final_bargraph', figure=bar_day))])


@app.callback(Output('output-container-date-picker-single', 'children'),
    Input('my_date_picker_single', 'date'))
def update_output(date_value):
    string_prefix = 'Travel Day: '
    if date_value is not None:
        date_object = date.fromisoformat(date_value)
        date_string = convert_date(date_value)
        return string_prefix + date_string
    
@app.callback(Output('final_output', "figure"),
              Input('my_date_picker_single', 'date'),
              Input('hours_dropdown_id', 'value'),
              Input('direction_id', 'value'))
def update_final_output_hour(my_date_picker_single, hours_dropdown_id, direction_id):
    starter_variables[1] = str(my_date_picker_single)
    starter_variables[2] = str(hours_dropdown_id)
    starter_variables[3] = str(direction_id)
    fig = predicted_figure(starter_variables)
    return fig

@app.callback(Output('final_bargraph', "figure"),
              Input('my_date_picker_single', 'date'))
def update_bar_graph(my_date_picker_single):
    day = convert_date(str(my_date_picker_single))
    df_filter = final_table[final_table['day']==day]
    color_map = {0:"#2bad4e", 1:"#85e043", 2:"#eff229", 3:"#f2a529", 4:"#f25829"}

    bar_day = make_subplots(shared_yaxes="all", rows=2, cols=2, start_cell="bottom-left",
                            subplot_titles=("Johor-Tuas", "Tuas-Johor",
                                            "Johor-Woodlands","Johor-Woodlands"))
    f1 = df_filter[df_filter['view']=='Johor-Tuas']
    c1 = pd.Series(f1['cat']).map(color_map)
    bar_day.add_trace(go.Bar(x=f1['hour'], y=f1['vehicle'], name='Johor-Tuas', showlegend=False, marker={'color':c1}),
                  row=1, col=1)

    f2 = df_filter[df_filter['view']=='Tuas-Johor']
    c2 = pd.Series(f2['cat']).map(color_map)
    bar_day.add_trace(go.Bar(x=f2['hour'], y=f2['vehicle'], name='Tuas-Johor', showlegend=False, marker={'color':c2}),
                  row=1, col=2)
    f3 = df_filter[df_filter['view']=='Johor-Woodlands']
    c3 = pd.Series(f3['cat']).map(color_map)
    bar_day.add_trace(go.Bar(x=f3['hour'], y=f3['vehicle'], name='Johor-Woodlands', showlegend=False, marker={'color':c3}),
                  row=2, col=1)
    f4 = df_filter[df_filter['view']=='Woodlands-Johor']
    c4 = pd.Series(f4['cat']).map(color_map)
    bar_day.add_trace(go.Bar(x=f4['hour'], y=f4['vehicle'], name='Johor-Woodlands', showlegend=False, marker={'color':c4}),
                  row=2, col=2)
    val_d = datetime.strptime(my_date_picker_single, "%Y-%m-%d").strftime("%d %B, %Y")
    tex = "Predicted 24 Hour Traffic Trend on: " + day + ", " + str(val_d)

    bar_day.update_layout(title_text=tex, paper_bgcolor="rgba(0,0,0,0)", plot_bgcolor="rgba(0,0,0,0)")
    bar_day.update_xaxes(tickangle=45)

    return bar_day
    
   
app.run_server(host="0.0.0.0", port=8053, debug=True)

Dash is running on http://0.0.0.0:8053/

Dash app running on http://0.0.0.0:8053/
